In [490]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import math
import folium
import utils


In [491]:
# Carregando o dataset
df_train = pd.read_csv('../data/treated_data/train.csv')
df_val = pd.read_csv('../data/treated_data/validation.csv')
df_test = pd.read_csv('../data/treated_data/test.csv')

In [492]:
# Função para converter RSSI em distância
def rssi_to_distance(rssi, A=-40, n=2):
    """
    Converte o RSSI em distância usando o modelo de perda de percurso.
    """
    try:
        return 10 ** ((A - rssi) / (10 * n))
    except Exception as e:
        print(f"Erro na conversão de RSSI para distância: {e}")
        return np.nan

In [493]:
def trilateration(p1, p2, p3, d1, d2, d3):
    """
    Calcula a posição (x, y) usando trilateração.
    """
    x1, y1 = p1
    x2, y2 = p2
    x3, y3 = p3

    A = np.array([
        [2 * (x2 - x1), 2 * (y2 - y1)],
        [2 * (x3 - x2), 2 * (y3 - y2)]
    ])

    B = np.array([
        [d1**2 - d2**2 - x1**2 + x2**2 - y1**2 + y2**2],
        [d2**2 - d3**2 - x2**2 + x3**2 - y2**2 + y3**2]
    ])

    try:
        pos = np.linalg.lstsq(A, B, rcond=None)[0]
        return pos[0][0], pos[1][0]
    except np.linalg.LinAlgError:
        print("Erro na resolução do sistema de equações de trilateração.")
        return None


In [494]:
antenas = {
    'rssi_1_1': (-8.04342, -34.952),
    'rssi_2_1': (-8.05289, -34.944672),
    'rssi_3_1': (-8.05532, -34.9579)
}


In [495]:
# Função para calcular a posição estimada para cada ponto
def calcular_posicoes(pontos_df, antenas):
    posicoes_estimadas = []

    for _, ponto in pontos_df.iterrows():
        # Obter RSSI para o ponto
        rssis = {
            'rssi_1_1': ponto['rssi_1_1'],
            'rssi_2_1': ponto['rssi_2_1'],
            'rssi_3_1': ponto['rssi_3_1']
        }

        # Converter RSSI para distâncias
        distancias = {grupo: rssi_to_distance(rssi) for grupo, rssi in rssis.items()}

                # Verificar se todas as distâncias são válidas
        if any(np.isnan(dist) for dist in distancias.values()):
            print(f"Distância inválida para ponto {ponto['ponto_id']}.")
            continue

        # Calcular a posição estimada
        posicao = trilateration(
            antenas['rssi_1_1'], antenas['rssi_2_1'], antenas['rssi_3_1'],
            distancias['rssi_1_1'], distancias['rssi_2_1'], distancias['rssi_3_1']
        )
        
        if posicao:
            posicoes_estimadas.append((ponto['ponto_id'], posicao))

    return posicoes_estimadas

In [496]:
# Calcular posições estimadas
posicoes_estimadas = calcular_posicoes(df_train, antenas)

In [497]:
# Criar o mapa centrado na área das antenas
mapa = folium.Map(location=[-8.05, -34.95], zoom_start=15)

In [498]:
# Adicionar as antenas ao mapa
for key, (lat, lon) in antenas.items():
    folium.Marker(
        location=[lat, lon],
        popup=f'Antenna {key}',
        icon=folium.Icon(color='black', icon='info-sign')
    ).add_to(mapa)


In [499]:
# Adicionar os pontos reais ao mapa
for _, ponto in df_train.iterrows():
    folium.CircleMarker(
        location=[ponto['lat'], ponto['lon']],
        radius=1,  
        color='blue',
        fill=True,
        fill_color='blue'
    ).add_to(mapa)

In [500]:
posicoes_estimadas

[(8790.0, (-8.05063919835139, -34.95196327821021)),
 (3227.0, (-8.050736740018698, -34.952049175449034)),
 (4180.0, (-8.050871716673699, -34.95190461342742)),
 (8922.0, (-8.050605466510243, -34.951799029885734)),
 (1117.0, (-8.050858888196705, -34.95188152934733)),
 (295.0, (-8.051091100810797, -34.95213033334471)),
 (9042.0, (-8.050851374333117, -34.95178702933033)),
 (5865.0, (-8.050810329820271, -34.95202576754865)),
 (7198.0, (-8.050771516682309, -34.951934212633766)),
 (1181.0, (-8.050858888196705, -34.95188152934733)),
 (3551.0, (-8.050833421673085, -34.95203141490924)),
 (9500.0, (-8.050504286153108, -34.952150246464505)),
 (4970.0, (-8.050783696328057, -34.95208111509986)),
 (7712.0, (-8.050746848789299, -34.95173770718674)),
 (6167.0, (-8.050767436364719, -34.95197033618619)),
 (9596.0, (-8.050717215762285, -34.95205745170416)),
 (2218.0, (-8.050749316102175, -34.95183103062515)),
 (2100.0, (-8.050745134866624, -34.95183946396467)),
 (5748.0, (-8.050797922167538, -34.952060994

In [501]:
# Adicionar os pontos estimados ao mapa
for ponto_id, (lat, lon) in posicoes_estimadas:
    folium.CircleMarker(
        location=[lat, lon],
        radius=1,  
        color='red',
        fill=True,
        fill_color='red'
    ).add_to(mapa)

In [502]:
mapa

In [503]:
#validação
# Calcular posições estimadas
posicoes_estimadas2 = calcular_posicoes(df_test, antenas)

In [504]:
mapa2 = folium.Map(location=[-8.05, -34.95], zoom_start=15)

In [505]:
# Adicionar as antenas ao mapa
for key, (lat, lon) in antenas.items():
    folium.Marker(
        location=[lat, lon],
        popup=f'Antenna {key}',
        icon=folium.Icon(color='black', icon='info-sign')
    ).add_to(mapa2)

In [506]:
# Adicionar os pontos estimados ao mapa
for ponto_id, (lat, lon) in posicoes_estimadas2:
    folium.CircleMarker(
        location=[lat, lon],
        radius=1,  
        color='red',
        fill=True,
        fill_color='red'
    ).add_to(mapa2)

In [508]:
posicoes_estimadas2

[(6506.0, (-8.050733007006203, -34.951925843005895)),
 (2557.0, (-8.051213841668233, -34.952288951783565)),
 (5560.0, (-8.050776766562777, -34.9520336546379)),
 (2050.0, (-8.050735221852452, -34.95185945802947)),
 (9326.0, (-8.05059190738745, -34.952167010111246)),
 (920.0, (-8.050898494516929, -34.951932712733324)),
 (726.0, (-8.051034977761232, -34.9520578053317)),
 (7734.0, (-8.050787127889063, -34.95173650427153)),
 (7576.0, (-8.050885602857836, -34.9524972659263)),
 (9286.0, (-8.050646385136675, -34.95196216538911)),
 (3845.0, (-8.050905929059033, -34.95194882621251)),
 (4242.0, (-8.050868439070216, -34.95190037776899)),
 (3389.0, (-8.050691136863076, -34.95205755280525)),
 (7385.0, (-8.050561998404618, -34.95203586155566)),
 (8808.0, (-8.050866268387475, -34.95176351858586)),
 (4223.0, (-8.050866043141934, -34.9518972815025)),
 (2975.0, (-8.05118091809652, -34.95224640453682)),
 (3067.0, (-8.050736740018698, -34.952049175449034)),
 (3476.0, (-8.050691136863076, -34.95205755280525

In [507]:
mapa2